# Plotting IAGOS data

This notebook is a demonstration on how to plot data from the IAGOS project in python

## Source Data

The source data for any plots in this notebook are the from [IAGOS](https://www.iagos.org/) research data which are gained by installing packages on passenger flights and are publicly available and licensed under the [Creative Commons Attribution 4.0 International licence (CC BY 4.0)](https://creativecommons.org/licenses/by/4.0/).

The Source data is provided as NetCDF files that among others usually have the following variables to analyse:

Base data:
- UTC_time
- lon
- lat

Data with validity flags (data_name_validity_flag)
- baro_alt_AC
- radio_alt_AC
- air_press_AC
- air_temp_AC
- air_speed_AC
- ground_speed_AC
- wind_dir_AC
- wind_speed_AC

Chemical measurement data (with name_error, name_validity_flag and name_process_flag):
- O3_PM
- CO_PM
- NOy_PM
- NO_PM
- NOx_PM

These variables of course might differ, depending on when the data was recorded. Newer files will have a `air_stag_temp_AC` instead of `air_temp_AC`



## Requirements

The data is plotted using the python cartopy package, which is based on matplotlib and shapely. Additionally, requests is used to request the data from the IAGOS API.

In case you do not have all of these requirements installed, try installing cartopy and requests via your preferred way (usually pip or conda)

### Troubleshooting Installation

Cartopy installation sadly tends to fail, especially when not installing it via conda, mainly because it requires GEOS

#### Debian

On Debian, you can install the required system libraries using the system package manager:

`sudo apt -y install libgeos-dev`

#### Windows

On Windows, you can try installing [OSGEO](https://www.osgeo.org/projects/osgeo4w/), and then install from the git repository:

```commandline
git clone https://github.com/SciTools/cartopy.git
cd cartopy
python setup.py build_ext -LC:\OSGeo4W\lib -IC:\OSGeo4W\include
python setup.py install
```

#### MacOS

On MacOS, you'll be able to install dependencies via:

```
brew install geos
pip3 install --upgrade pyshp
# shapely needs to be built from source to link to geos. If it is already
# installed, uninstall it by: pip3 uninstall shapely
pip3 install "shapely<2" --no-binary shapely
```

After installing the dependencies, please try

`pip3 install cartopy`

again.

## Implementation

### Imports

Firstly, we'll need to import several packages.

In [ ]:
import os
import sys
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import cartopy.io.img_tiles as cimgt
import netCDF4 as nC
import numpy as np
from requests import TooManyRedirects, Timeout, HTTPError, get

### Getting Data from IAGOS

Then, let's get the flight path data from IAGOS using python requests:

In [ ]:
def get_file(flight_id):
    url = f"https://services.iagos-data.fr/prod/v2.0/downloads/{flight_id}?level=2&format=netcdf&type=timeseries"
    try:
        response = get(url)
    except ConnectionError:
        print("There was a network problem. Try again please")
        return
    except HTTPError:
        print("HTTP request returned an unsuccessful status code. Try again please.")
        return
    except Timeout:
        print("The request timed out. Try again please")
        return
    except TooManyRedirects:
        print("The request was redirected the maximum number of times. Try again please")
        return
    if response.status_code != 200:
        print(
            "It looks like getting the file for that flight ID was not possible. If you provided the flight ID yourself, it is likely "
            "the case that the ID provided did not exist."
        )
        sys.exit()
    open("source.nc4", "wb").write(response.content)

### Plotting functionality
Let's also create a class that is able to plot data.

The dataset is read from the file we downloaded above and then plotted onto a custom map using the functions we just defined

In [ ]:
class Plot:

    def __init__(self, param):
        self.dataset: nC.Dataset = nC.Dataset("source.nc4")
        self.fig: plt.figure = plt.figure()
        self.ax = self.fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
        self.data = param
        os.remove("source.nc4")

    def get_lon(self):
        return self.dataset["lon"][:]

    def get_lat(self):
        return self.dataset["lat"][:]

    def get_data(self):
        return self.dataset[self.data][:]

    def handle_03_data(self):
        data = self.get_data()
        data[data < 0] = 0
        return data

    def plot(self):
        # use terrain
        stamen_terrain = cimgt.Stamen("terrain-background")
        self.ax.add_image(stamen_terrain, 3)
        # plot the points measured
        self.ax.plot(self.get_lon(), self.get_lat(), linewidth=1, color="blue", transform=ccrs.PlateCarree())
        # scatter according to data points
        self.ax.scatter(self.get_lon(), self.get_lat(), c=np.sqrt(self.handle_03_data()), cmap="jet", s=np.divide(self.handle_03_data(), 2), transform=ccrs.PlateCarree())
        # customize map
        west = -135
        east = 20
        south = 10
        north = 60
        self.ax.set_extent([west, east, south, north])
        self.ax.add_feature(cfeature.LAND)
        self.ax.add_feature(cfeature.OCEAN)
        self.ax.add_feature(cfeature.COASTLINE, edgecolor="#888888", linestyle="-", linewidth=0.5)
        self.ax.add_feature(cfeature.BORDERS, linestyle=":", linewidth=0.5)  # '', ' ', 'None', '--', '-.', '-', ':'
        self.ax.add_feature(cfeature.LAKES, alpha=0.5)        
    
    def show(self):
        plt.show()

### Plotting an example flight path
 Finally, let's plot the flight `2005010612051151` with regard to Ozone. (size and colour)

In [ ]:
flight_id = "2005010612051151"
param = "O3_PM"
get_file(flight_id)
plot = Plot(param)
plot.plot()
plot.show()